In [1]:
%pip install -Uq prophet

Note: you may need to restart the kernel to use updated packages.



[notice] A new release of pip is available: 25.0.1 -> 25.1.1
[notice] To update, run: python.exe -m pip install --upgrade pip


In [3]:
%pip install snowflake-connector-python

Defaulting to user installation because normal site-packages is not writeable
     ---------------------------------------- 0.0/774.4 kB ? eta -:--:--
     ------------------------- ------------ 524.3/774.4 kB 6.2 MB/s eta 0:00:01
     -------------------------------------- 774.4/774.4 kB 5.5 MB/s eta 0:00:00
  Installing build dependencies: started
  Installing build dependencies: finished with status 'done'
  Getting requirements to build wheel: started
  Getting requirements to build wheel: finished with status 'done'
  Preparing metadata (pyproject.toml): started
  Preparing metadata (pyproject.toml): finished with status 'done'
   ---------------------------------------- 0.0/13.6 MB ? eta -:--:--
   --------- ------------------------------ 3.1/13.6 MB 15.3 MB/s eta 0:00:01
   ----------------------- ---------------- 8.1/13.6 MB 19.2 MB/s eta 0:00:01
   ---------------------------------------  13.4/13.6 MB 21.3 MB/s eta 0:00:01
   ---------------------------------------- 13.6/13.6 


[notice] A new release of pip is available: 25.0.1 -> 25.1.1
[notice] To update, run: python.exe -m pip install --upgrade pip


In [6]:
import snowflake.connector
import json

import pandas as pd
from prophet import Prophet
import logging

In [5]:
def ejecutar_consulta_snowflake_df(sql_query: str):
    account = "WKJWFSY-LI12007"
    user = "PACORTIZ9"
    password = "Tacosdepastor,13"
    database = "SNOWFLAKE_SAMPLE_DATA"
    schema = "TPCH_SF1"

    conn = None
    try:
        conn = snowflake.connector.connect(
            account=account,
            user=user,
            password=password,
            database=database,
            schema=schema
        )
        cursor = conn.cursor()
        cursor.execute(sql_query)
        results = pd.DataFrame(cursor.fetchall(), columns=[col[0] for col in cursor.description])
        return results
    except snowflake.connector.errors.Error as e:
        print(f"Error al ejecutar la consulta en Snowflake: {e}")
        return pd.DataFrame()  # Retorna un DataFrame vacío en caso de error
    finally:
        if conn:
            cursor.close()
            conn.close()

In [14]:
consulta_sql = """
SELECT
    DATE_TRUNC('MONTH', O.O_ORDERDATE) AS SALES_MONTH,
    P.P_TYPE,
    N.N_NAME AS COUNTRY_NAME,
    SUM(L.L_QUANTITY) AS TOTAL_MONTHLY_QUANTITY
FROM
    LINEITEM AS L
JOIN
    PART AS P ON L.L_PARTKEY = P.P_PARTKEY
JOIN
    ORDERS AS O ON L.L_ORDERKEY = O.O_ORDERKEY
JOIN
    CUSTOMER AS C ON O.O_CUSTKEY = C.C_CUSTKEY
JOIN
    NATION AS N ON C.C_NATIONKEY = N.N_NATIONKEY
GROUP BY
    DATE_TRUNC('MONTH', O.O_ORDERDATE),
    P.P_TYPE,
    N.N_NAME
ORDER BY
    SALES_MONTH,
    P.P_TYPE,
    N.N_NAME;
"""

In [15]:
df_historico = ejecutar_consulta_snowflake_df(consulta_sql)
if df_historico.empty:
    print("No se obtuvieron resultados de la consulta.")

In [16]:
df_historico

SALES_MONTH                  P_TYPE   COUNTRY_NAME  \
0       1992-01-01  ECONOMY ANODIZED BRASS        ALGERIA   
1       1992-01-01  ECONOMY ANODIZED BRASS      ARGENTINA   
2       1992-01-01  ECONOMY ANODIZED BRASS         BRAZIL   
3       1992-01-01  ECONOMY ANODIZED BRASS         CANADA   
4       1992-01-01  ECONOMY ANODIZED BRASS          CHINA   
...            ...                     ...            ...   
298928  1998-08-01   STANDARD POLISHED TIN        ROMANIA   
298929  1998-08-01   STANDARD POLISHED TIN         RUSSIA   
298930  1998-08-01   STANDARD POLISHED TIN   SAUDI ARABIA   
298931  1998-08-01   STANDARD POLISHED TIN  UNITED STATES   
298932  1998-08-01   STANDARD POLISHED TIN        VIETNAM   

       TOTAL_MONTHLY_QUANTITY  
0                      526.00  
1                      635.00  
2                      565.00  
3                      595.00  
4                      514.00  
...                       ...  
298928                  98.00  
298929                  64.00  
298930                  24.00  
298931                  61.00  
298932                 137.00  

[298933 rows x 4 columns]

In [17]:
# Opcional: Para suprimir los mensajes informativos de Prophet durante el entrenamiento
logging.getLogger('prophet').setLevel(logging.WARNING)

# Asegúrate de que la columna de fecha sea de tipo datetime
df_historico['SALES_MONTH'] = pd.to_datetime(df_historico['SALES_MONTH'])

# Prophet requiere que el DataFrame de entrada tenga dos columnas: 'ds' (para la fecha) y 'y' (para el valor a predecir).

# Obtener todas las combinaciones únicas de producto y país
unique_combinations = df_historico[['P_TYPE', 'COUNTRY_NAME']].drop_duplicates()

# Lista para almacenar los resultados de la predicción
all_forecasts = []


In [18]:
# --- Iterar y entrenar un modelo Prophet para cada serie ---
for index, row in unique_combinations.iterrows():
    product_type = row['P_TYPE']
    country_name = row['COUNTRY_NAME']

    print(f"Pronosticando para: Tipo de Producto='{product_type}', País='{country_name}'")

    # Filtrar los datos para la combinación actual
    series_data = df_historico[
        (df_historico['P_TYPE'] == product_type) &
        (df_historico['COUNTRY_NAME'] == country_name)
    ].copy()

    # Preparar el DataFrame para Prophet: renombrar columnas a 'ds' y 'y'
    series_data = series_data.rename(columns={
        'SALES_MONTH': 'ds',
        'TOTAL_MONTHLY_QUANTITY': 'y'
    })

    # Asegurarse de que 'ds' sea datetime y 'y' sea numérico
    series_data['ds'] = pd.to_datetime(series_data['ds'])
    series_data['y'] = pd.to_numeric(series_data['y'])

    # Si la serie tiene pocos puntos de datos, Prophet puede fallar. Se recomienda al menos 2 periodos estacionales.
    # Para series mensuales, significa al menos 24 meses. Si tienes menos, el pronóstico podría no ser fiable.
    if len(series_data) < 24: # Umbral sugerido, ajusta según tu confianza en la estacionalidad
        print(f"  Advertencia: Pocos datos ({len(series_data)} meses) para '{product_type}' en '{country_name}'. Omitiendo o el pronóstico será menos fiable.")
        # continue # Descomentar para omitir series con pocos datos

    # Inicializar y ajustar el modelo Prophet
    # seasonality_mode='multiplicative' suele ser bueno para la demanda de productos
    # daily_seasonality=False, weekly_seasonality=False porque estamos a nivel mensual
    m = Prophet(
        yearly_seasonality=True,
        weekly_seasonality=False,
        daily_seasonality=False,
        seasonality_mode='multiplicative'
    )
    m.fit(series_data)

    # Crear un DataFrame con las fechas futuras para los próximos 6 meses
    # Primero, encuentra la última fecha en tus datos históricos
    last_date = series_data['ds'].max()
    future = m.make_future_dataframe(periods=6, freq='MS') # 'MS' para el inicio del mes
    future = future[future['ds'] > last_date] # Solo los 6 meses futuros

    # Asegurarse de que 'future' no esté vacío (puede pasar si ya tienes datos para el mes actual que coincide con el inicio de la predicción)
    if future.empty:
        print(f"  No se generaron fechas futuras para '{product_type}' en '{country_name}'. Es posible que ya tengas datos para el periodo de pronóstico.")
        continue


    # Realizar la predicción
    forecast = m.predict(future)

    # Añadir las columnas de tipo de producto y país a las predicciones
    forecast['P_TYPE'] = product_type
    forecast['COUNTRY_NAME'] = country_name

    # Seleccionar las columnas relevantes (fecha, predicción, intervalos de confianza)
    forecast_subset = forecast[['ds', 'yhat', 'yhat_lower', 'yhat_upper', 'P_TYPE', 'COUNTRY_NAME']]
    all_forecasts.append(forecast_subset)

Pronosticando para: Tipo de Producto='ECONOMY ANODIZED BRASS', País='ALGERIA'


18:01:00 - cmdstanpy - INFO - Chain [1] start processing
18:01:01 - cmdstanpy - INFO - Chain [1] done processing


Pronosticando para: Tipo de Producto='ECONOMY ANODIZED BRASS', País='ARGENTINA'


18:01:02 - cmdstanpy - INFO - Chain [1] start processing
18:01:02 - cmdstanpy - INFO - Chain [1] done processing
18:01:02 - cmdstanpy - INFO - Chain [1] start processing


Pronosticando para: Tipo de Producto='ECONOMY ANODIZED BRASS', País='BRAZIL'


...

18:29:18 - cmdstanpy - INFO - Chain [1] done processing
18:29:18 - cmdstanpy - INFO - Chain [1] start processing


Pronosticando para: Tipo de Producto='STANDARD POLISHED TIN', País='UNITED STATES'


18:29:18 - cmdstanpy - INFO - Chain [1] done processing
18:29:19 - cmdstanpy - INFO - Chain [1] start processing


Pronosticando para: Tipo de Producto='STANDARD POLISHED TIN', País='VIETNAM'


18:29:19 - cmdstanpy - INFO - Chain [1] done processing


In [19]:
# Consolidar todas las predicciones en un solo DataFrame ---
if all_forecasts:
    final_predictions_df = pd.concat(all_forecasts)
    final_predictions_df = final_predictions_df.rename(columns={
        'ds': 'Mes de Predicción',
        'yhat': 'Demanda Predicha (Cantidad)',
        'yhat_lower': 'Límite Inferior (95% CI)',
        'yhat_upper': 'Límite Superior (95% CI)'
    })
    final_predictions_df = final_predictions_df[[
        'Mes de Predicción',
        'P_TYPE',
        'COUNTRY_NAME',
        'Demanda Predicha (Cantidad)',
        'Límite Inferior (95% CI)',
        'Límite Superior (95% CI)'
    ]]

    # Opcional: Redondear las cantidades predichas, ya que la demanda debe ser un número entero
    final_predictions_df['Demanda Predicha (Cantidad)'] = final_predictions_df['Demanda Predicha (Cantidad)'].round().astype(int)
    final_predictions_df['Límite Inferior (95% CI)'] = final_predictions_df['Límite Inferior (95% CI)'].round().astype(int)
    final_predictions_df['Límite Superior (95% CI)'] = final_predictions_df['Límite Superior (95% CI)'].round().astype(int)

    print("\n--- Tabla de Predicciones Final ---")
    print(final_predictions_df.to_string()) # Usar .to_string() para ver todo el DataFrame sin truncar
else:
    print("No se generaron predicciones.")



--- Tabla de Predicciones Final ---
  Mes de Predicción                     P_TYPE    COUNTRY_NAME  Demanda Predicha (Cantidad)  Límite Inferior (95% CI)  Límite Superior (95% CI)
0        1998-09-01     ECONOMY ANODIZED BRASS         ALGERIA                          450                       326                       574
1        1998-10-01     ECONOMY ANODIZED BRASS         ALGERIA                          556                       429                       680
2        1998-11-01     ECONOMY ANODIZED BRASS         ALGERIA                          389                       260                       512
3        1998-12-01     ECONOMY ANODIZED BRASS         ALGERIA                          462                       336                       587
4        1999-01-01     ECONOMY ANODIZED BRASS         ALGERIA                          449                       329                       570
5        1999-02-01     ECONOMY ANODIZED BRASS         ALGERIA                          410        